In [22]:
from datasets import load_dataset
import json
from copy import deepcopy
dataset = load_dataset("ncbi_disease",split='test')
dataset[1]


{'id': '1',
 'tokens': ['Ataxia',
  '-',
  'telangiectasia',
  '(',
  'A',
  '-',
  'T',
  ')',
  'is',
  'a',
  'recessive',
  'multi',
  '-',
  'system',
  'disorder',
  'caused',
  'by',
  'mutations',
  'in',
  'the',
  'ATM',
  'gene',
  'at',
  '11q22',
  '-',
  'q23',
  '(',
  'ref',
  '.',
  '3',
  ')',
  '.'],
 'ner_tags': [1,
  2,
  2,
  0,
  1,
  2,
  2,
  0,
  0,
  0,
  1,
  2,
  2,
  2,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0]}

In [23]:
def construct_output(tokens, ner_tags):
    tag_open=False
    output=""
    token_copy = deepcopy(tokens)
    inserted_start=0
    inserted_end=0
    for i in range(len(tokens)):
        if ner_tags[i]==1:
            token_copy.insert(i+inserted_start,'@')
            inserted_start+=1
            print(token_copy)
    
    for i in range(len(ner_tags)-1):
        if ner_tags[i]==1 and ner_tags[i+1]==0:
            token_copy.insert(i+2*inserted_end+2,'#')
            inserted_end+=1
        elif ner_tags[i]==2 and ner_tags[i+1]==0:
            token_copy.insert(i+2*inserted_end+2,'#')
            inserted_end+=1
        
        print(token_copy)

    if len(ner_tags)>0 and ner_tags[len(ner_tags)-1]!=0:
        token_copy.append('#')

    return ' '.join(token_copy)           

In [24]:
io_pair={'id': [],
         'input': [],
         'output':[]}
for row in dataset:
    print(row)
    io_pair['id'].append(row['id'])
    inp=' '.join(row['tokens'])
    out=construct_output(row['tokens'], row['ner_tags'])
    io_pair['input'].append(inp)
    io_pair['output'].append(out)
    print(row['id'])
    print(inp)
    print(out)
fp=open('responses_test.json','w')

json.dump(io_pair,fp)
fp.close()

{'id': '0', 'tokens': ['Clustering', 'of', 'missense', 'mutations', 'in', 'the', 'ataxia', '-', 'telangiectasia', 'gene', 'in', 'a', 'sporadic', 'T', '-', 'cell', 'leukaemia', '.'], 'ner_tags': [0, 0, 0, 0, 0, 0, 1, 2, 2, 0, 0, 0, 1, 2, 2, 2, 2, 0]}
['Clustering', 'of', 'missense', 'mutations', 'in', 'the', '@', 'ataxia', '-', 'telangiectasia', 'gene', 'in', 'a', 'sporadic', 'T', '-', 'cell', 'leukaemia', '.']
['Clustering', 'of', 'missense', 'mutations', 'in', 'the', '@', 'ataxia', '-', 'telangiectasia', 'gene', 'in', 'a', '@', 'sporadic', 'T', '-', 'cell', 'leukaemia', '.']
['Clustering', 'of', 'missense', 'mutations', 'in', 'the', '@', 'ataxia', '-', 'telangiectasia', 'gene', 'in', 'a', '@', 'sporadic', 'T', '-', 'cell', 'leukaemia', '.']
['Clustering', 'of', 'missense', 'mutations', 'in', 'the', '@', 'ataxia', '-', 'telangiectasia', 'gene', 'in', 'a', '@', 'sporadic', 'T', '-', 'cell', 'leukaemia', '.']
['Clustering', 'of', 'missense', 'mutations', 'in', 'the', '@', 'ataxia', '-', 

In [25]:
print(io_pair['input'][10])
print(io_pair['output'][10])

The evidence of a significant proportion of loss - of - function mutations and a complete absence of the normal copy of ATM in the majority of mutated tumours establishes somatic inactivation of this gene in the pathogenesis of sporadic T - PLL and suggests that ATM acts as a tumour suppressor .
The evidence of a significant proportion of loss - of - function mutations and a complete absence of the normal copy of ATM in the majority of mutated @ tumours # establishes somatic inactivation of this gene in the pathogenesis of @ sporadic T - PLL # and suggests that ATM acts as a @ tumour # suppressor .


In [28]:
import pandas as pd
df = pd.DataFrame(io_pair,index=io_pair['id'])

In [29]:
df

id                                              input  \
0      0  Clustering of missense mutations in the ataxia...   
1      1  Ataxia - telangiectasia ( A - T ) is a recessi...   
2      2  The risk of cancer , especially lymphoid neopl...   
3      3  By analysing tumour DNA from patients with spo...   
4      4  In marked contrast to the ATM mutation pattern...   
..   ...                                                ...   
936  936  In an attempt to resolve this issue , we have ...   
937  937  These reagents detect a 220 - kD protein local...   
938  938  Immunohistochemical staining of human breast s...   
939  939  Conversely , BRCA1 expression was reduced or u...   
940  940                                                      

                                                output  
0    Clustering of missense mutations in the @ atax...  
1    @ Ataxia - telangiectasia # ( @ A - T # ) is a...  
2    The risk of @ cancer # , especially @ lymphoid...  
3    By analysing @ tumour # DNA from patients with...  
4    In marked contrast to the ATM mutation pattern...  
..                                                 ...  
936  In an attempt to resolve this issue , we have ...  
937  These reagents detect a 220 - kD protein local...  
938  Immunohistochemical staining of human breast s...  
939  Conversely , BRCA1 expression was reduced or u...  
940                                                     

[941 rows x 3 columns]